# Install & Import Packages

In [1]:
!git clone https://github.com/LightTag/sequence-labeling-with-transformers.git
!mv sequence-labeling-with-transformers/sequence_aligner sequence_aligner
!pip install transformers accelerate evaluate
!pip install seqeval

Cloning into 'sequence-labeling-with-transformers'...
remote: Enumerating objects: 26, done.
remote: Counting objects: 100% (26/26), done.
remote: Compressing objects: 100% (24/24), done.
remote: Total 26 (delta 6), reused 16 (delta 1), pack-reused 0
Unpacking objects: 100% (26/26), 459.10 KiB | 3.33 MiB/s, done.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 59.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 219.1/219.1 kB 26.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 29.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 117.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.6/474.6 kB 55.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 16.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
import torch
from torch.utils.data import DataLoader, random_split

from transformers import BertTokenizerFast, BertForTokenClassification, BertForTokenClassification
from transformers import AutoTokenizer, AdamW, Trainer, TrainingArguments, AutoModel, AutoModelForTokenClassification, DataCollatorForTokenClassification

from sequence_aligner.labelset import LabelSet
from sequence_aligner.dataset import  TrainingDataset
from sequence_aligner.containers import TraingingBatch

from seqeval.metrics import accuracy_score, classification_report, f1_score

import warnings
warnings.filterwarnings('ignore')

# Load Dataset: 

In [4]:
tokenizer = BertTokenizerFast.from_pretrained('bert-base-cased')

dataset = torch.load("/content/drive/MyDrive/Colab Notebooks/hkust_urop/dataset.pt")
IDX = 2
# The original text:
print(dataset.texts[IDX])
# Decode the input IDs:
print(tokenizer.decode(dataset[IDX].input_ids))

** Adani Ports and Special Economic Zone Ltd <APSE.NS> said National Company Law Tribunal has approved acquisition of Gangavaram Port. [nFWN31B02L]
* * Adani Ports and Special Economic Zone Ltd < APSE. NS > said National Company Law Tribunal has approved acquisition of Gangavaram Port. [ nFWN31B02L ] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [P

In [5]:
# consistent dataset

const_dataset = torch.load("/content/drive/MyDrive/Colab Notebooks/hkust_urop/const.pt")
IDX = 2
print(const_dataset.texts[IDX])
print(tokenizer.decode(const_dataset[IDX].input_ids))

Brent crude <LCOc1> rose 1.4% to $100.69 per barrel and U.S. crude <CLc1> was also up by 1.4% to $100.61 a barrel.
Brent crude < LCOc1 > rose 1. 4 % to $ 100. 69 per barrel and U. S. crude < CLc1 > was also up by 1. 4 % to $ 100. 61 a barrel. [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [

# Split Dataset

In [6]:
# Use train_ds to train the model
# Use val_ds to adjust the hyperparamaters
# Use test_ds to report your work!
train_ds, val_ds, test_ds = random_split(
    dataset=dataset,
    lengths=[int(0.7*len(dataset)), 
             int(0.2*len(dataset)), 
             len(dataset) - int(0.9*len(dataset))],
)

const_train_ds, const_val_ds, const_test_ds = random_split(
    dataset=const_dataset,
    lengths=[int(0.7*len(const_dataset)), 
             int(0.2*len(const_dataset)), 
             len(const_dataset) - int(0.9*len(const_dataset))],
)


In [ ]:
# train_ds, val_ds, test_ds are not dict
const_train_ds[-1]

TrainingExample(input_ids=[1109, 156, 111, 153, 2260, 4909, 1826, 7448, 133, 119, 16625, 26161, 26351, 135, 1896, 124, 119, 122, 110, 117, 4703, 1111, 1103, 1148, 1159, 1107, 1421, 1552, 1105, 1521, 4291, 1348, 12535, 119, 7882, 17901, 133, 119, 16625, 26161, 16647, 135, 3152, 123, 119, 129, 110, 119, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], attention_masks=[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

In [ ]:
# checking labels' length in each dataset
print(len(train_ds[0].labels), len(val_ds[0].labels), len(test_ds[0].labels))

250 250 250


In [7]:
# convert the TrainingExample to dict for easier implementation
def dataset(input_ds):
    output_ds = []

    for d in range(len(input_ds)):
        data_dict = {}
        data_dict["input_ids"] = torch.tensor(input_ds[d].input_ids)
        data_dict["attention_masks"] = torch.tensor(input_ds[d].attention_masks)
        data_dict["labels"]=torch.tensor(input_ds[d].labels)
        
        output_ds.append(data_dict)
    

    return output_ds


In [8]:
# turn all the ds into a list of dict
train_ds_dict = dataset(train_ds)
val_ds_dict = dataset(val_ds)
test_ds_dict = dataset(test_ds)

const_train_ds_dict = dataset(const_train_ds)
const_val_ds_dict = dataset(const_val_ds)
const_test_ds_dict = dataset(const_test_ds)


In [9]:
const_train_ds_dict[0]

{'input_ids': tensor([  158,  9782, 22018,  1474,  1115,   789,  1103,  3501,  2255,  1103,
           143, 13041,  1658,  1674,  1136,  1444,  1106,  4693,  5600,  1118,
          1851,   171,  3491,  1110,  1115,  1152,  1169,  4344,   170,  2299,
          3507,   117, 23847,  2798,  2975,  1748,  1105,  1202,  1177,  1107,
           170,  1167,  3442,  4571,  1105,  1750, 26499,  2109,  1236,   119,
           790,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,   

# Build Model

In [10]:
from torch import cuda
device = 'cuda' if cuda.is_available() else 'cpu'
print(device)

cuda


In [11]:
# define data collator
data_collator = DataCollatorForTokenClassification(tokenizer)

In [12]:
label_dict = {
    0: 'O',
    1: "B-Positive",
    2: "I-Positive",
    3: "L-Positive",
    4: "U-Positive",
    5: "B-Negative",
    6: "I-Negative",
    7: "L-Negative",
    8: "U-Negative",
    9: "B-Neutral",
    10: "I-Neutral",
    11: "L-Neutral",
    12: "U-Neutral",
    -100: "[PAD]",
}

In [13]:
id2label = {
    0: 'O',
    1: "B-Positive",
    2: "I-Positive",
    3: "L-Positive",
    4: "U-Positive",
    5: "B-Negative",
    6: "I-Negative",
    7: "L-Negative",
    8: "U-Negative",
    9: "B-Neutral",
    10: "I-Neutral",
    11: "L-Neutral",
    12: "U-Neutral",
}

label2id = {
    "O": 0,
    "B-Positive": 1,
    "I-Positive": 2,
    "L-Positive": 3,
    "U-Positive": 4,
    "B-Negative": 5,
    "I-Negative": 6,
    "L-Negative": 7,
    "U-Negative": 8,
    "B-Neutral": 9,
    "I-Neutral": 10,
    "L-Neutral": 11,
    "U-Neutral": 12,
}

In [26]:
# loading model
checkpoint = 'bert-base-cased'

# BertForTokenClassification
bertModel = BertForTokenClassification.from_pretrained(checkpoint, num_labels=13, id2label=id2label, label2id=label2id)

# AutoModelForTokenClassification
autoModel = AutoModelForTokenClassification.from_pretrained(checkpoint, num_labels=13, id2label=id2label, label2id=label2id)

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForTokenClassification: ['cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-cas

In [15]:
import numpy as np
import evaluate
from datasets import load_metric

seqeval = evaluate.load("seqeval")

def compute_metrics(p):
    predictions, labels = p
    predictions = np.argmax(predictions, axis=2)

    true_predictions = [
        [label_dict[p] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(predictions, labels)
    ]
    true_labels = [
        [label_dict[l] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(predictions, labels)
    ]

    results = seqeval.compute(predictions=true_predictions, references=true_labels)
    return {
        "precision": results["overall_precision"],
        "recall": results["overall_recall"],
        "f1": results["overall_f1"],
        "accuracy": results["overall_accuracy"],
    }




In [16]:
# compare the prediction and the original labels
def showPred(test_dataset, labels_pred):

  labels_mask = [[label_dict[x] for x in y['labels'].tolist()]for y in test_dataset]

  for idx in range(len(labels_pred)):
    print("="*20)
    print(print(tokenizer.decode(test_ds[idx].input_ids)))
    print(f"mask: {labels_mask[idx]}")
    print(f"pred:{labels_pred[idx]}")

In [17]:
# show seqeval evalution F1 and classification report
def seqeval_eval(test_dataset, labels_pred):
  labels_mask = [[label_dict[x] for x in y['labels'].tolist()]for y in test_dataset]

  f1 = f1_score(labels_mask, labels_pred)
  print(f"f1 score: {f1:.5f}")
  print(classification_report(labels_mask, labels_pred))

In [18]:
# add early stopping

from transformers import EarlyStoppingCallback
early_stopping = EarlyStoppingCallback(early_stopping_patience=7, early_stopping_threshold=0.01)

In [19]:
from huggingface_hub import login
login()

### BERT Model

In [ ]:
# declare training argument

batch_size = 16
logging_steps = 625

training_args = TrainingArguments(
    output_dir="./content",
    num_train_epochs=30,
    learning_rate=5e-5,
    weight_decay=0.01,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=32,
    save_strategy="epoch",
    evaluation_strategy="epoch",
    fp16=True,
    # push_to_hub=True,
    load_best_model_at_end=True,
)


In [ ]:
# declare trainer
bert_trainer = Trainer(
    bertModel,
    training_args,
    train_dataset=train_ds_dict,
    eval_dataset=val_ds_dict,
    data_collator=data_collator,
    tokenizer=tokenizer,
    callbacks=[early_stopping],
    compute_metrics=compute_metrics
)

In [ ]:
bert_trainer.train()

TrainOutput(global_step=1557, training_loss=0.061412015172557795, metrics={'train_runtime': 599.4559, 'train_samples_per_second': 138.025, 'train_steps_per_second': 8.658, 'total_flos': 3167262266301000.0, 'train_loss': 0.061412015172557795, 'epoch': 9.0})

In [ ]:
# Evaluate the bert model

eval_result = bert_trainer.evaluate()
for key, value in eval_result.items():
  print(f"{key}: {value:.4f}")

eval_loss: 0.1036
eval_precision: 0.2547
eval_recall: 0.3124
eval_f1: 0.2806
eval_accuracy: 0.9662
eval_runtime: 5.2514
eval_samples_per_second: 150.0560
eval_steps_per_second: 4.7610
epoch: 9.0000


In [ ]:
# labels prediction for test dataset
bert_trainer_pred = bert_trainer.predict(test_ds_dict)
pred_labels = np.argmax(bert_trainer_pred.predictions, axis=-1)
pred_labels

array([[ 0,  0,  0, ...,  0,  0,  0],
       [ 0,  0,  0, ...,  0,  0,  0],
       [ 0, 10, 10, ...,  0,  0,  0],
       ...,
       [ 0,  0,  0, ...,  0,  0,  0],
       [ 0,  0,  0, ...,  0,  0,  0],
       [ 0,  0,  0, ...,  0,  0,  0]])

In [ ]:
print(test_ds_dict[30]['labels'].tolist())
print(pred_labels[30].tolist())

[0, 0, 0, 0, 0, 0, 9, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100,

In [ ]:
# labels predictions
labels_pred = [[label_dict[x] for x in y]for y in pred_labels]
showPred(test_ds_dict, labels_pred)

Union members have been holding protests this week to bring attention to their demands. Billie Adeosun, a Starbucks employee since 2015 who works at a unionized location in Olympia, said on Monday higher wages were a top priority. [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [

In [ ]:
# evaluation from seqeval
seqeval_eval(test_ds_dict, labels_pred)

f1 score: 0.02694
              precision    recall  f1-score   support

    Negative       0.00      0.00      0.00        62
     Neutral       0.05      0.45      0.09       204
        PAD]       0.00      0.00      0.00       395
    Positive       0.00      0.05      0.00        60

   micro avg       0.02      0.13      0.03       721
   macro avg       0.01      0.13      0.02       721
weighted avg       0.01      0.13      0.02       721



## Auto Model

In [ ]:
# declare training arguments
auto_training_args = TrainingArguments(
    output_dir="./content",
    num_train_epochs=30,
    learning_rate=2e-5,
    weight_decay=0,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    save_strategy="epoch",
    evaluation_strategy="epoch",
    fp16=True,
    # push_to_hub=True,
    load_best_model_at_end=True,
)


In [ ]:
# declare trainer
auto_trainer = Trainer(
    autoModel,
    auto_training_args,
    train_dataset=train_ds_dict,
    eval_dataset=val_ds_dict,
    data_collator=data_collator,
    tokenizer=tokenizer,
    callbacks=[early_stopping],
    compute_metrics=compute_metrics
)

In [ ]:
auto_trainer.train()

TrainOutput(global_step=1384, training_loss=0.02884377978440654, metrics={'train_runtime': 606.6168, 'train_samples_per_second': 136.396, 'train_steps_per_second': 8.556, 'total_flos': 2815344236712000.0, 'train_loss': 0.02884377978440654, 'epoch': 8.0})

In [ ]:
# Evaluate the auto model
eval_result = auto_trainer.evaluate()
for key, value in eval_result.items():
  print(f"{key}: {value:.4f}")

eval_loss: 0.1075
eval_precision: 0.3750
eval_recall: 0.3223
eval_f1: 0.3467
eval_accuracy: 0.9693
eval_runtime: 4.6352
eval_samples_per_second: 170.0030
eval_steps_per_second: 10.7870
epoch: 8.0000


In [ ]:
# labels prediction for test dataset
auto_trainer_pred =auto_trainer.predict(test_ds_dict)
pred_labels = np.argmax(auto_trainer_pred.predictions, axis=-1)
pred_labels

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [ ]:
labels_pred = [[label_dict[x] for x in y]for y in pred_labels]
showPred(test_ds_dict, labels_pred)

In fairness to Philadelphia though, since its teams have been champions far more often than the Astros, which won the world series only once, in 2017, there is a better chance of a Phillies'win coinciding with a recession. [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PA

In [ ]:
seqeval_eval(labels_pred)

f1 score: 0.11028
              precision    recall  f1-score   support

    Negative       0.17      0.02      0.03        62
     Neutral       0.28      0.32      0.30       204
        PAD]       0.00      0.00      0.00       395
    Positive       0.03      0.37      0.06        60

   micro avg       0.10      0.12      0.11       721
   macro avg       0.12      0.18      0.10       721
weighted avg       0.10      0.12      0.09       721



# Training with consistent dataset

## BERT Model (consistent ver.)

In [ ]:
# define training argument
training_args = TrainingArguments(
    output_dir="./content",
    num_train_epochs=100,
    learning_rate=2e-5,
    weight_decay=0,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    save_strategy="epoch",
    evaluation_strategy="epoch",
    fp16=True,
    # push_to_hub=True,
    load_best_model_at_end=True,
)


In [ ]:
# declare trainer
bert_trainer = Trainer(
    bertModel,
    training_args,
    train_dataset=const_train_ds_dict,
    eval_dataset=const_val_ds_dict,
    data_collator=data_collator,
    tokenizer=tokenizer,
    callbacks=[early_stopping],
    compute_metrics=compute_metrics
)

In [ ]:
bert_trainer.train()

You're using a BertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=780, training_loss=0.1215688332533225, metrics={'train_runtime': 323.7053, 'train_samples_per_second': 253.317, 'train_steps_per_second': 16.064, 'total_flos': 1569467644650000.0, 'train_loss': 0.1215688332533225, 'epoch': 15.0})

In [ ]:
# Evaluate the bert model
eval_result = bert_trainer.evaluate()
for key, value in eval_result.items():
  print(f"{key}: {value:.4f}")

eval_loss: 0.1169
eval_precision: 0.6933
eval_recall: 0.7712
eval_f1: 0.7302
eval_accuracy: 0.9720
eval_runtime: 2.5257
eval_samples_per_second: 92.6460
eval_steps_per_second: 5.9390
epoch: 15.0000


In [ ]:
# labels prediction for test dataset
bert_trainer_pred = bert_trainer.predict(const_test_ds_dict)
pred_labels = np.argmax(bert_trainer_pred.predictions, axis=-1)
pred_labels

array([[ 9, 10, 10, ...,  0,  0,  0],
       [ 0,  0,  0, ...,  1,  1,  1],
       [ 0,  0,  0, ...,  1,  1,  1],
       ...,
       [ 0,  9, 11, ...,  0,  0,  0],
       [ 0,  0,  0, ...,  9,  9,  9],
       [ 9, 10, 11, ...,  5,  5,  5]])

In [ ]:
labels_pred = [[label_dict[x] for x in y]for y in pred_labels]
showPred(const_test_ds_dict, labels_pred)

The ISO projected power demand would reach 46, 278 megawatts ( MW ) on Friday and 35, 013 MW on Saturday. That compares with the preliminary record of 52, 061 MW on Tuesday, which broke the prior all - time high of 50, 270 MW in 2006. [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PA

In [ ]:
seqeval_eval(const_test_ds_dict, labels_pred)

f1 score: 0.02782
              precision    recall  f1-score   support

    Negative       0.01      0.86      0.01        49
     Neutral       0.09      0.80      0.16       133
        PAD]       0.00      0.00      0.00       118
    Positive       0.01      0.50      0.01        56

   micro avg       0.01      0.50      0.03       356
   macro avg       0.03      0.54      0.05       356
weighted avg       0.04      0.50      0.06       356



## Auto Model (consistent ver.)

In [27]:
# declare training arguments
auto_training_args = TrainingArguments(
    output_dir="./content",
    num_train_epochs=100,
    learning_rate=2e-5,
    weight_decay=0,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    save_strategy="epoch",
    evaluation_strategy="epoch",
    fp16=True,
    # push_to_hub=True,
    load_best_model_at_end=True,
)

In [28]:
# declare trainer
auto_trainer = Trainer(
    autoModel,
    auto_training_args,
    train_dataset=const_train_ds_dict,
    eval_dataset=const_val_ds_dict,
    data_collator=data_collator,
    tokenizer=tokenizer,
    callbacks=[early_stopping],
    compute_metrics=compute_metrics
)

In [29]:
auto_trainer.train()

TrainOutput(global_step=572, training_loss=0.15570511851277385, metrics={'train_runtime': 240.4735, 'train_samples_per_second': 340.994, 'train_steps_per_second': 21.624, 'total_flos': 1150942939410000.0, 'train_loss': 0.15570511851277385, 'epoch': 11.0})

In [30]:
# Evaluate the bert model
eval_result = auto_trainer.evaluate()
for key, value in eval_result.items():
  print(f"{key}: {value:.4f}")

eval_loss: 0.1459
eval_precision: 0.4493
eval_recall: 0.5496
eval_f1: 0.4944
eval_accuracy: 0.9506
eval_runtime: 1.4212
eval_samples_per_second: 164.6470
eval_steps_per_second: 10.5540
epoch: 11.0000


In [31]:
# labels prediction for test dataset
auto_trainer_pred = auto_trainer.predict(const_test_ds_dict)
pred_labels = np.argmax(auto_trainer_pred.predictions, axis=-1)
pred_labels

array([[ 0,  0,  0, ...,  7,  7,  7],
       [ 0,  9, 10, ...,  7,  7,  7],
       [ 0,  0,  0, ...,  1,  1,  1],
       ...,
       [ 0,  0,  0, ...,  7,  7,  7],
       [ 9, 11,  0, ...,  7,  7,  7],
       [ 0,  0,  0, ...,  7,  7,  7]])

In [32]:
labels_pred = [[label_dict[x] for x in y]for y in pred_labels]
showPred(const_test_ds_dict, labels_pred)

The draft DMA sets out a list of dos and don'ts for online gatekeepers, in effect targeting Apple < AAPL. O >, Alphabet < GOOGL. O > unit Google, Facebook parent Meta < FB. O >, Amazon < AMZN. O > and Microsoft < MSFT. O >. [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [P

In [33]:
seqeval_eval(const_test_ds_dict, labels_pred)

f1 score: 0.17317
              precision    recall  f1-score   support

    Negative       0.00      0.02      0.00        51
     Neutral       0.35      0.79      0.48       139
        PAD]       0.00      0.00      0.00       118
    Positive       0.05      0.55      0.09        56

   micro avg       0.11      0.39      0.17       364
   macro avg       0.10      0.34      0.15       364
weighted avg       0.14      0.39      0.20       364

